# Face Recognition Demo

In [54]:
%reload_ext autoreload
%autoreload 2

import os
from os.path import join
from glob import glob
from random import randint
from pathlib import Path

import numpy as np
import pandas as pd
import cv2 as cv
%matplotlib inline
import matplotlib.pyplot as plt

import sys
sys.path.append('/work/megapixels_dev/megapixels/')
from app.settings import app_cfg as cfg
from app.utils import im_utils, file_utils
from app.models.bbox import BBox
from app.settings import types
from app.utils import draw_utils
from app.models.data_store import DataStore

In [15]:
data_store = DataStore(types.DataStore.HDD, types.Dataset.VGG_FACE2)

## Load metadata

In [44]:
fp_records = data_store.metadata(types.Metadata.FILE_RECORD)
fp_roi = data_store.metadata(types.Metadata.FACE_ROI)
fp_roi = fp_roi.replace('face_roi.csv', 'face_roi_0_1000.csv')
fp_bbox_vgg = '/data_store/datasets/people/vgg_face2/downloads/bb_landmark/loose_bb_test.csv'

df_records = pd.read_csv(fp_records).set_index('index')
df_roi = pd.read_csv(fp_roi).set_index('index')
df_bbox_vgg = pd.read_csv(fp_bbox_vgg).set_index('NAME_ID')

## Compare ROI sizes

In [24]:
rois = df_roi.to_dict()
records = df_records.to_dict()

In [104]:
import math

In [126]:
from app.models.bbox import BBox

deltas_cxy = []
deltas_width = []
deltas_height = []

for roi_idx, ds_roi in df_roi.iterrows():
  bbox = BBox.from_xywh(ds_roi.x, ds_roi.y, ds_roi.w, ds_roi.h)
  file_record = df_records.iloc[int(ds_roi.record_index)]
  dim = (file_record.width, file_record.height)
  bbox_dim = bbox.to_dim(dim)
  name_id = join(file_record.subdir.split('/')[1], file_record.fn)
  ds_vgg_bbox = df_bbox_vgg.loc[name_id]
  roi_vgg = (ds_vgg_bbox.X, ds_vgg_bbox.Y, ds_vgg_bbox.W, ds_vgg_bbox.H)
  bbox_vgg = BBox.from_xywh_dim(ds_vgg_bbox.X, ds_vgg_bbox.Y, ds_vgg_bbox.W, ds_vgg_bbox.H, dim)
  bbox_vgg_dim = bbox_vgg.to_dim(dim)
  w,h = dim
  dx, dy = ((bbox_vgg_dim.cx - bbox_vgg_dim.cx)/w, (bbox_vgg_dim.cy - bbox_dim.cy)/h)
  dw, dh = (abs(bbox_vgg_dim.w - bbox_dim.w)/w, abs(bbox_vgg_dim.h - bbox_dim.h)/h)
  delta_center = math.sqrt(math.pow(dx/dim[0],2) + math.pow(dy/dim[1],2))
  deltas_width.append(dw)
  deltas_height.append(dh)
  deltas_cxy.append(delta_center)

In [127]:
mu_c = np.mean(np.array(deltas_cxy))
mu_w = np.mean(np.array(deltas_width))
mu_h = np.mean(np.array(deltas_height))
print(f'average c offset: {mu_c}')
print(f'average w offset: {mu_w}')
print(f'average h offset: {mu_h}')

average c offset: 0.0002713261298150514
average w offset: 0.03440484078308657
average h offset: 0.03306552311371902


In [ ]:
cv.INTER_

In [27]:
# fp_im = data_store.face(file_record.subdir, file_record.fn, file_record.ext)
# im = cv.imread(fp_im)
# im = draw_utils.draw_bbox(im, bbox_dim, color=(0,255,0))
# im = draw_utils.draw_bbox(im, bbox_vgg_dim, color=(0,0,255))
# # expand bbox
# bbox_expanded = bbox.expand(0.3)
# bbox_expanded_dim = bbox_expanded.to_dim(dim)
# im = draw_utils.draw_bbox(im, bbox_expanded_dim, color=(255,0,0))
# plt.imshow(cv.cvtColor(im, cv.COLOR_BGR2RGB))
# # load image and draw bbox

{'h': {0: 0.4681763648986816,
  1: 0.4431796967983246,
  2: 0.4864671230316162,
  3: 0.5021313428878784,
  4: 0.4792057275772095,
  5: 0.5172641277313232,
  6: 0.5529294013977051,
  7: 0.5571120381355286,
  8: 0.4725810289382935,
  9: 0.4759339094161987,
  10: 0.489094614982605,
  11: 0.4840135872364044,
  12: 0.6406047344207764,
  13: 0.67110276222229,
  14: 0.49501633644104,
  15: 0.4962148666381836,
  16: 0.5188913345336914,
  17: 0.5239598751068115,
  18: 0.5352462530136108,
  19: 0.5095468759536743,
  20: 0.5045645236968994,
  21: 0.5334460735321045,
  22: 0.5757352113723755,
  23: 0.5194357633590698,
  24: 0.4840328395366669,
  25: 0.4736475944519043,
  26: 0.5025535821914673,
  27: 0.5299184322357178,
  28: 0.4940259456634522,
  29: 0.5005787014961243,
  30: 0.9954201579093932,
  31: 0.9872612953186036,
  32: 0.502242922782898,
  33: 0.6007291674613953,
  34: 0.6096506118774414,
  35: 0.5998443365097046,
  36: 0.5508362054824829,
  37: 0.5466625690460205,
  38: 0.552003979682922